# Instrument integration example (synthesis_bots)

Communication between instruments in the automation system uses the ØMQ framework implemented through [pyzmq](https://github.com/zeromq/pyzmq). In particular, we are utilizing ØMQ's broadcast and subscription capabilities, the scheduler facilitates seamless communication between the host PC and various devices. This enables efficient command dissemination and feedback collection, enhancing the responsiveness and reliability of the automation process. 

## Integration on the client side

The main class for instrument connectivity (`WorkflowEntity()`) can be found in `synthesis_bots.utils.entity`. Its main functionality is to handle TCP connection, disconnection, awaiting commands from the host and command execution. The `synthesis_bots.utils.entity.Instrument` enum class enumerates the implemented instruments, so this also has to be extended when integration is completed.

### Important settings for a new WorkflowEntity integration

Each instrument that is integrated into the workflow needs to have its unique TCP address with a port specified, as well as a list of accepted workflows. Those are specified in the `settings.toml` file, where the `workflows` table contains a location of the Python script that is executed upon receiving the command. Example `setting.toml` entires for the NMR integration within our laboratory would be as follows:

```toml
[tcp]

HOST      = "tcp://172.31.1.17:5558"
NMR       = "tcp://172.31.1.15:5552"

[workflows.NMR]

Supramol_Screening   = "synthesis_bots.workflows.nmr.supramol.screening"
Supramol_Replication = "synthesis_bots.workflows.nmr.supramol.replication"
Supramol_HostGuest   = "synthesis_bots.workflows.nmr.supramol.host_guest"
```

In which case, the `main()` function from the `synthesis_bots/workflows/nmr/supramol/screening.py` would be executed when the host broadcasts the `Supramol_Screening` command to the NMR entity.


### Integration into the main code

The package is typically run as a script and the `__main__.py` needs to handle device connectivity. As different instruments might require proprietary licensed control software, instrument-related packages are not added directly to the package dependencies. Hence, manually adding the corresponding `elif` clause is the preferred solution when integrating a new instrument so that all the potential dependencies can be handled in one place directly. Example for the NMR integration within `__main__.py` would be as follows:

```python
elif sys.argv[1] == "NMR":
        module = find_spec("fourier_nmr_driver")
        if module is None:
            logger.critical("No NMR driver installed.")
            raise ImportError("fourier_nmr_driver not found.")

        nmr = WorkflowEntity(
            instrument_address=SETTINGS["tcp"]["NMR"],
            host_address=SETTINGS["tcp"]["HOST"],
            instrument=Instrument.NMR,
        )

        nmr.connect()
        sys.exit(nmr.await_command())

```

### Important PC settings

It is worth ensuring that the TCP/IP address of the instrument control PC is set to static and that any power saving options related to the network card are disabled. In case of Windows 10/11 PCs, that might also imply disconnecting the ethernet cable if the instrument is connected through a wireless network without Internet access.

## Integration on the host side

Finally, the NMR needs to be added to the host broadcaster, which loops through existing entities and sends them the corresponding commands at each workflow step:

```python
import zmq
import time
 
def send_command(command, entity):
    try:
        context = zmq.Context()
        socket = context.socket(zmq.PUB)
        socket.connect(f"tcp://{entity['ip']}:{entity['port']}")
        socket.send_multipart(entity['topic'].encode(), command.encode()])
        print(f"Sent command '{command}' to {entity['name']}")
        socket.close()

    except Exception as e:
        print(f"Error sending command to {entity['name']}: {e}")
 
if __name__ == "__main__":
    entities = [
        {
            "name":"NMR", 
            "topic": "NMR", 
            "ip": "172.31.1.15", 
            "port": "5552"
        },
        ...
    ]
 
    while True:
        for entity in entities:
            command = input(f"Enter command for {entity['name']}: ")
            send_command(command, entity)
        time.sleep(1)

```